# Team 6 Final Project
Chaim Gross, Eytan Slotnik, Tomer Fried, Naftali Arnold
## Week 6

 check correlation between cont_date and cont_doy and identifier of reporter

In [27]:
import pandas as pd
import sqlite3
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
import plotly.express as px
import numpy as np
import datetime

# EDA

In [28]:
pd.set_option('display.max_columns', None)

In [29]:
conn = sqlite3.connect('FPA_FOD_20170508.sqlite')
raw_df = pd.read_sql_query("SELECT * from Fires", conn)
raw_df["STAT_CAUSE_CODE"] = raw_df["STAT_CAUSE_CODE"].astype(int)

In [30]:
X, y = raw_df.drop(columns = ["STAT_CAUSE_CODE"]), raw_df.filter(items = ["STAT_CAUSE_CODE"])

In [31]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.25, random_state=1)

Let's investigate the data, using ProfileReport

In [32]:
df = X_train.merge(y_train, left_index=True, right_index=True)

In [33]:
# from pandas_profiling import ProfileReport
# profile = ProfileReport(df)
# profile.to_file("data_report.html")

After going through the data, we have chosen features that should be dropped based on:
- Many missing values
- High cardinality
- Features which provide data, that is already provided by other features
- Low correlation with any other feature
- Common sense for unnecessary features

In [34]:
columns_to_drop = ['OBJECTID', 'FOD_ID', 'FPA_ID', 'NWCG_REPORTING_UNIT_ID',
                   'NWCG_REPORTING_UNIT_NAME', 'SOURCE_REPORTING_UNIT', 'SOURCE_REPORTING_UNIT_NAME', 'LOCAL_FIRE_REPORT_ID',
                   'LOCAL_INCIDENT_ID', 'FIRE_CODE', 'FIRE_NAME', 'ICS_209_INCIDENT_NUMBER', 'ICS_209_NAME', 'MTBS_ID', 'MTBS_FIRE_NAME','COMPLEX_NAME', 'OWNER_CODE', 'COUNTY', 'FIPS_CODE', 'FIPS_NAME', "Shape"]

df = df.drop(columns = columns_to_drop)

Points to think about from the EDA:
* New feature might be: length of fire. discovery minus contain. wh
* State feature - maybe we should do binning on high-cardinality values
* Most fires occur in specific fay of the year and specific time
* It seems like in different longitudes, the fires are common in different days of the year.
* Correlation stat_code and system_type should be checked
* Even though dropped, OWNER_CODE is highly correlated with other features and should be re-considered in the future.
* Maybe, interseting feature engineering can be done using  "NWCG_REPORTING_UNIT_ID", "FOD_ID"


# Missing Values

Let's check which features, out of the filtered ones, have missing values or "" values:

In [35]:
df.info()
(df == "").any()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 470116 entries, 138183 to 128037
Data columns (total 18 columns):
 #   Column                 Non-Null Count   Dtype  
---  ------                 --------------   -----  
 0   SOURCE_SYSTEM_TYPE     470116 non-null  object 
 1   SOURCE_SYSTEM          470116 non-null  object 
 2   NWCG_REPORTING_AGENCY  470116 non-null  object 
 3   FIRE_YEAR              470116 non-null  int64  
 4   DISCOVERY_DATE         470116 non-null  float64
 5   DISCOVERY_DOY          470116 non-null  int64  
 6   DISCOVERY_TIME         249395 non-null  object 
 7   STAT_CAUSE_DESCR       470116 non-null  object 
 8   CONT_DATE              247195 non-null  float64
 9   CONT_DOY               247195 non-null  float64
 10  CONT_TIME              227117 non-null  object 
 11  FIRE_SIZE              470116 non-null  float64
 12  FIRE_SIZE_CLASS        470116 non-null  object 
 13  LATITUDE               470116 non-null  float64
 14  LONGITUDE              470116 n

SOURCE_SYSTEM_TYPE       False
SOURCE_SYSTEM            False
NWCG_REPORTING_AGENCY    False
FIRE_YEAR                False
DISCOVERY_DATE           False
DISCOVERY_DOY            False
DISCOVERY_TIME           False
STAT_CAUSE_DESCR         False
CONT_DATE                False
CONT_DOY                 False
CONT_TIME                 True
FIRE_SIZE                False
FIRE_SIZE_CLASS          False
LATITUDE                 False
LONGITUDE                False
OWNER_DESCR              False
STATE                    False
STAT_CAUSE_CODE          False
dtype: bool

In [36]:
df["CONT_TIME"][df["CONT_TIME"] == ""] = None # There are entries in "CONT_TIME" with value "", so for the sake of unity, we fill it with None.

C:\Users\t-tomerfried\AppData\Local\Temp\ipykernel_20248\2484478842.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Features with missing values:
- DISCOVERY_TIME
- CONT_DATE
- CONT_DOY
- CONT_TIME

Their missing values are correlated with each other, along with "LOCAL_FRIE_REPORT_ID", "FIRE_CODE", "FIRE_NAME".
Let's take a look at the null values of them

In [37]:
discovery_time_missing = raw_df[raw_df["DISCOVERY_TIME"].isnull()].filter(items = ["DISCOVERY_TIME", "CONT_DATE", "CONT_DOY", "CONT_TIME", "LOCAL_FRIE_REPORT_ID" , "FIRE_CODE", "FIRE_NAME"])
discovery_time_missing

DISCOVERY_TIME  CONT_DATE  CONT_DOY CONT_TIME FIRE_CODE  \
0                None        NaN       NaN      None      None   
3                None        NaN       NaN      None      None   
4                None        NaN       NaN      None      None   
8                None        NaN       NaN      None      None   
10               None        NaN       NaN      None      None   
...               ...        ...       ...       ...       ...   
626808           None        NaN       NaN      None      None   
626809           None        NaN       NaN      None      None   
626811           None        NaN       NaN      None      None   
626820           None        NaN       NaN      None      None   
626821           None        NaN       NaN      None      None   

                        FIRE_NAME  
0                            None  
3                            None  
4                            None  
8                            None  
10                           None  
...                           ...  
626808  HWY 152  E/ RD 8           
626809                       None  
626811                       None  
626820  BRANCIFORTE DR  SOQUEL 5   
626821                       None  

[294076 rows x 6 columns]

In [38]:
cont_date_doy_missing = raw_df[raw_df["CONT_DATE"].isnull()].filter(items = ["LOCAL_FRIE_REPORT_ID", "CONT_DATE", "CONT_DOY", "CONT_TIME", "FIRE_CODE", "FIRE_NAME"])
cont_date_doy_missing


CONT_DATE  CONT_DOY CONT_TIME FIRE_CODE                  FIRE_NAME
0             NaN       NaN      None      None                       None
3             NaN       NaN      None      None                       None
4             NaN       NaN      None      None                       None
6             NaN       NaN      None      None                       None
7             NaN       NaN      None      None                       None
...           ...       ...       ...       ...                        ...
626809        NaN       NaN      None      None                       None
626811        NaN       NaN      None      None                       None
626814        NaN       NaN      None      None     MS0    0808-3310326003
626820        NaN       NaN      None      None  BRANCIFORTE DR  SOQUEL 5 
626821        NaN       NaN      None      None                       None

[297088 rows x 5 columns]

In [39]:
cont_time_missing = raw_df[raw_df["CONT_TIME"].isnull()].filter(items = ["CONT_TIME", "LOCAL_FRIE_REPORT_ID", "CONT_DATE", "CONT_DOY", "FIRE_CODE", "FIRE_NAME"])
cont_time_missing

CONT_TIME  CONT_DATE  CONT_DOY FIRE_CODE                  FIRE_NAME
0           None        NaN       NaN      None                       None
3           None        NaN       NaN      None                       None
4           None        NaN       NaN      None                       None
6           None        NaN       NaN      None                       None
7           None        NaN       NaN      None                       None
...          ...        ...       ...       ...                        ...
626809      None        NaN       NaN      None                       None
626811      None        NaN       NaN      None                       None
626814      None        NaN       NaN      None     MS0    0808-3310326003
626820      None        NaN       NaN      None  BRANCIFORTE DR  SOQUEL 5 
626821      None        NaN       NaN      None                       None

[323724 rows x 5 columns]

We can see that entries with null values at one feature, are also null in the others, mostly.

Let's do a histogram of "discovery date - contain_date" (differentiating each other)

In [40]:
no_missing = df.dropna()
px.histogram(df["CONT_DOY"] - df["DISCOVERY_DOY"])

we can see that The majority of the fires are contained in the same day, and after, in the day after it.
Therefore, we will impute the missing values of "CONT_DATE" with "DISCOVERY_DATE" and "CONT_DOY" with "DISCOVERY_DOY" (for now).

In [41]:
empty_indices = df['CONT_DOY'][df['CONT_DOY'].isna()].index
df.loc[:, 'CONT_DOY' ].loc[empty_indices] = df.loc[:,'DISCOVERY_DOY' ].loc[empty_indices]
df.loc[:, 'CONT_DATE'].loc[empty_indices] = df.loc[:,'DISCOVERY_DATE'].loc[empty_indices]
df.loc[:, 'CONT_TIME'].loc[empty_indices] = df.loc[:,'DISCOVERY_TIME'].loc[empty_indices]

C:\Users\t-tomerfried\AppData\Local\Temp\ipykernel_20248\1898532659.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\t-tomerfried\AppData\Local\Temp\ipykernel_20248\1898532659.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\t-tomerfried\AppData\Local\Temp\ipykernel_20248\1898532659.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Let's focus now on 'DISCOVERY_TIME', "CONT_TIME".
Maybe we can try to predict them using linear regression

In [42]:
features_with_missing = {'DISCOVERY_TIME' : None, "CONT_TIME" : None}
regression_features = ['FIRE_YEAR', 'DISCOVERY_DATE', 'DISCOVERY_DOY']

for feature_name in features_with_missing:
    without_missing = df.loc[~df[feature_name].isnull()]
    without_missing[feature_name] = without_missing[feature_name].astype("float")
    X = without_missing.filter(items = regression_features)
    y = without_missing[feature_name]
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.25, random_state=0)
    regr = LinearRegression().fit(X_train,y_train)
    preds = regr.predict(X_test)
    features_with_missing[feature_name] = pd.DataFrame({"y_test" : y_test, "preds" : preds})

C:\Users\t-tomerfried\AppData\Local\Temp\ipykernel_20248\1490943440.py:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\t-tomerfried\AppData\Local\Temp\ipykernel_20248\1490943440.py:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



As we can see, the predicted values of "DISCOVERY_TIME" are between 14:00 - 15:00
and the predicted values of "CONT_TIME" are between 15:00 - 16:00

Options for imputing the missing values of "DISCOVERY_TIME" and "CONT_TIME":
    - impute them with mean value, without regression_features
    - impute with prediction from linear regression
    - dropping them out

Because we have approximately 300,000 missing values for every feature of them, mean imputing will be considered as a huge
bias. Also, it looks like linear regression predicts values which are close to the mean value.

Therefore, for now we will drop these features.

In [43]:
df = df.drop(columns=["DISCOVERY_TIME", "CONT_TIME"])

Next time work:
- Automatic One-hot encoding and label encoding
- Baseline model that works
- Manual One-hot encoding and label encoding
- complete missing values imputation

## Second thought, conversion, and dropping of features

Let's explore the categorical features and decide what to do with them:

In [44]:
categorical_features = df.select_dtypes(include=["object"])
for f in categorical_features.columns:
    print("\nValues:\n" + str(df[f].value_counts()) + "\n")


Values:
NONFED       340631
FED          119998
INTERAGCY      9487
Name: SOURCE_SYSTEM_TYPE, dtype: int64


Values:
ST-NASF        177686
DOI-WFMI        59857
FS-FIRESTAT     55257
ST-CACDF        21802
ST-NCNCS        16416
ST-GAGAS        16203
ST-MSMSS        15046
ST-TXTXS        14504
ST-ALALS        13901
ST-SCSCS        12209
ST-FLFLS        11236
IA-PRIITF        5522
FWS-FMIS         4884
ST-ORORS         4629
ST-LALAS         4072
ST-OKOKS         3927
ST-TNTNS         3701
ST-WIWIS         3641
ST-ARARS         2797
ST-VAVAS         2666
IA-HIWMO         2525
ST-MOMOS         2497
ST-WAWAS         2440
ST-MEMES         1834
ST-KYKYS         1629
ST-UTUTS         1091
ST-NMNMS         1066
IA-AKACC          919
ST-AZAZS          891
FA-NFIRS          863
ST-SDSDS          860
ST-CTCTS          857
ST-MTMTS          660
ST-COCOS          595
ST-MIMIS          532
IA-ICS209         521
ST-WYWYS          374
ST-NENES            6
Name: SOURCE_SYSTEM, dtype: int64


Values:
ST

One-Hot Encoding:
- SOURCE_SYSTEM_TYPE
- STATE

Label Encoding:
- FIRE_SIZE_CLASS (might require some sort of transformation because on lonear)

Might be leakage, Dropping:
- SOURCE_SYSTEM
- NWCG_REPORTING_AGENCY
- STAT_CAUSE_DESCR

Dropping:
- OWNER_DESCR


In [45]:
numeric_features = df.select_dtypes(include=[np.number])
for f in numeric_features.columns:
    print("\nValues:\n" + str(df[f].value_counts()) + "\n")


Values:
2006    28489
2000    24344
2007    23955
2011    22609
1999    22343
2005    22116
2001    21711
2008    21339
2010    20312
2009    19478
1996    18949
1994    18859
2002    18755
2015    18571
2012    18245
1995    17654
1998    17184
2003    17125
2004    17116
1992    17017
2014    16768
2013    16251
1993    15476
1997    15450
Name: FIRE_YEAR, dtype: int64


Values:
2454506.5    303
2455611.5    294
2453441.5    283
2453798.5    273
2456112.5    259
            ... 
2448999.5      1
2452259.5      1
2450807.5      1
2449001.5      1
2448951.5      1
Name: DISCOVERY_DATE, Length: 8760, dtype: int64


Values:
185    3159
186    2956
108    2386
101    2353
100    2295
       ... 
351     342
350     342
348     308
359     305
366     132
Name: DISCOVERY_DOY, Length: 366, dtype: int64


Values:
2454506.5    305
2455611.5    284
2453441.5    279
2453798.5    269
2453799.5    256
            ... 
2448999.5      1
2452259.5      1
2450783.5      1
2457388.5      1
2448951.5 

Dropping:
- DISCOVERY DATE - but to extract months, is weekend, is holiday
- DISCOVERY_DOY
- CONT_DOY - but to create feature of difference between discovery and contain day of year
- CONT_DATE
- FIRE_SIZE

One-Hot Encoding:
- months
- FIRE_YEAR

other notes:
- LATITUDE AND LONGITUDE might be problematic, but still usefull. Plus feature extraction might be usefull.



In [46]:
def create_date_faetures(df):
    """
    creates data features from YEAR and DOY.
    create a new column of date which is calculated from FIRE_YEAR and DISCOVERY_DOY, and extract from there features
    :param df: data
    :return: a new dataframe containing only the features we added
    """
    from pandas.tseries.holiday import USFederalHolidayCalendar as calendar

    features = pd.DataFrame()
    df["DISCOVERY_DATE"] = pd.to_datetime(df['FIRE_YEAR'] * 1000 + df['DISCOVERY_DOY'], format='%Y%j')
    cal = calendar()

    # is holiday feature
    holidays = cal.holidays(start=df["DISCOVERY_DATE"].min(), end=df["DISCOVERY_DATE"].max())
    features['IS_HOLIDAY'] = df['DISCOVERY_DATE'].isin(holidays)

    # is weekend feature
    features['IS_WEEKEND'] = dayofweek = df["DISCOVERY_DATE"].dt.dayofweek
    features['IS_WEEKEND'][dayofweek >= 5] = 1
    features['IS_WEEKEND'][dayofweek < 5]  = 0

    # month dummies
    month_dummies = pd.get_dummies(df["DISCOVERY_DATE"].dt.month, prefix="MONTH", drop_first=True)
    features = pd.concat([features, month_dummies], axis=1)

    return features

features = create_date_faetures(df)
df = df.merge(features, left_index=True, right_index=True)

C:\Users\t-tomerfried\AppData\Local\Temp\ipykernel_20248\3772951067.py:20: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\t-tomerfried\AppData\Local\Temp\ipykernel_20248\3772951067.py:21: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [48]:
# Feature dropping
df = df.drop(columns=["OWNER_DESCR", "DISCOVERY_DATE", "DISCOVERY_DOY", "CONT_DOY", "CONT_DATE", "FIRE_SIZE",
                      "SOURCE_SYSTEM", "NWCG_REPORTING_AGENCY", "STAT_CAUSE_DESCR"])

# One-Hot Encoding
for f in ['SOURCE_SYSTEM_TYPE', 'STATE', 'FIRE_YEAR']: # add months
    df = pd.get_dummies(df,prefix=[f], columns = [f], drop_first=True)

# Ordinal Encoding
from sklearn import preprocessing
le = preprocessing.LabelEncoder()
le.fit(df['FIRE_SIZE_CLASS'])
df['FIRE_SIZE_CLASS'] = le.transform(df['FIRE_SIZE_CLASS']) + 1

This is what we have got:

In [50]:
df.head()

FIRE_SIZE_CLASS   LATITUDE   LONGITUDE  STAT_CAUSE_CODE  IS_HOLIDAY  \
138183                2  31.248900  -93.176700                9       False   
519285                2  34.816700  -79.433300                9       False   
116246                2  38.697800 -112.172580               13       False   
179264                1  48.256667 -115.970000                1       False   
517587                2  33.218889 -117.128889                2       False   

        IS_WEEKEND  MONTH_2  MONTH_3  MONTH_4  MONTH_5  MONTH_6  MONTH_7  \
138183           0        1        0        0        0        0        0   
519285           0        1        0        0        0        0        0   
116246           0        0        0        0        0        0        1   
179264           0        0        0        0        0        0        0   
517587           0        0        0        0        0        0        1   

        MONTH_8  MONTH_9  MONTH_10  MONTH_11  MONTH_12  \
138183        0        0         0         0         0   
519285        0        0         0         0         0   
116246        0        0         0         0         0   
179264        1        0         0         0         0   
517587        0        0         0         0         0   

        SOURCE_SYSTEM_TYPE_INTERAGCY  SOURCE_SYSTEM_TYPE_NONFED  STATE_AL  \
138183                             0                          1         0   
519285                             0                          1         0   
116246                             0                          1         0   
179264                             0                          0         0   
517587                             0                          1         0   

        STATE_AR  STATE_AZ  STATE_CA  STATE_CO  STATE_CT  STATE_DC  STATE_DE  \
138183         0         0         0         0         0         0         0   
519285         0         0         0         0         0         0         0   
116246         0         0         0         0         0         0         0   
179264         0         0         0         0         0         0         0   
517587         0         0         1         0         0         0         0   

        STATE_FL  STATE_GA  STATE_HI  STATE_IA  STATE_ID  STATE_IL  STATE_IN  \
138183         0         0         0         0         0         0         0   
519285         0         0         0         0         0         0         0   
116246         0         0         0         0         0         0         0   
179264         0         0         0         0         0         0         0   
517587         0         0         0         0         0         0         0   

        STATE_KS  STATE_KY  STATE_LA  STATE_MA  STATE_MD  STATE_ME  STATE_MI  \
138183         0         0         1         0         0         0         0   
519285         0         0         0         0         0         0         0   
116246         0         0         0         0         0         0         0   
179264         0         0         0         0         0         0         0   
517587         0         0         0         0         0         0         0   

        STATE_MN  STATE_MO  STATE_MS  STATE_MT  STATE_NC  STATE_ND  STATE_NE  \
138183         0         0         0         0         0         0         0   
519285         0         0         0         0         1         0         0   
116246         0         0         0         0         0         0         0   
179264         0         0         0         1         0         0         0   
517587         0         0         0         0         0         0         0   

        STATE_NH  STATE_NJ  STATE_NM  STATE_NV  STATE_NY  STATE_OH  STATE_OK  \
138183         0         0         0         0         0         0         0   
519285         0         0         0         0         0         0         0   
116246         0         0         0         0         0         0         0   
179264         0    

In [51]:
X_train, y_train = df.drop(columns = ["STAT_CAUSE_CODE"]), df.filter(items = ["STAT_CAUSE_CODE"])

In [52]:
from sklearn.metrics import classification_report
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score

rf = RandomForestClassifier(random_state=10).fit(X_train, y_train)
rf_preds = rf.predict(X_train)
print("Random Forest accuracy score is:")
print(accuracy_score(y_train,rf_preds))
print("Random Forest F1 score is:")
print(classification_report(y_train,rf_preds, zero_division=0))

C:\Users\t-tomerfried\AppData\Local\Temp\ipykernel_20248\1041348616.py:5: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().



Random Forest accuracy score is:
0.9983535978354279
Random Forest F1 score is:
              precision    recall  f1-score   support

           1       1.00      1.00      1.00     69786
           2       1.00      1.00      1.00     36954
           3       1.00      1.00      1.00     13143
           4       1.00      1.00      1.00     18980
           5       1.00      1.00      1.00    107275
           6       1.00      1.00      1.00      8300
           7       1.00      1.00      1.00     70126
           8       0.99      0.99      0.99     15215
           9       1.00      1.00      1.00     81400
          10       1.00      1.00      1.00      2871
          11       1.00      1.00      1.00      3556
          12       1.00      1.00      1.00       942
          13       1.00      1.00      1.00     41568

    accuracy                           1.00    470116
   macro avg       1.00      1.00      1.00    470116
weighted avg       1.00      1.00      1.00    470116



## Next Time:
- Scaling and transformations on features
- Feature engineering and extraction
- Base model
- functionzing pre preprocessing for test data
- checking other things to do in shifter's notebooks
